In [7]:
### Cargamos el modelo phi-4
from transformers import AutoTokenizer, AutoModelForCausalLM, pipeline

model_id = "microsoft/phi-4-mini-instruct"
tokenizer = AutoTokenizer.from_pretrained(model_id)
model_lm = AutoModelForCausalLM.from_pretrained(model_id, device_map="auto", torch_dtype="auto")
generator = pipeline("text-generation", model=model_lm, tokenizer=tokenizer)

c:\Users\PC\Maestria\NLP\RAG\venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
`torch_dtype` is deprecated! Use `dtype` instead!
Loading checkpoint shards: 100%|██████████| 2/2 [00:02<00:00,  1.36s/it]
Device set to use cuda:0


In [8]:
prompt = "<|user|>\n¿Qué indica un valor alto del índice SDI en el agua de alimentación de RO?\n<|assistant|>"
respuesta = generator(prompt, max_new_tokens=256, do_sample=True, temperature=0.5)[0]["generated_text"]
respuesta

'<|user|>\n¿Qué indica un valor alto del índice SDI en el agua de alimentación de RO?\n<|assistant|>El Índice de Desalinización de Agua de Alimentación (SDI) es una medida utilizada para evaluar la calidad del agua de alimentación de un sistema de Filtración por Reverse Osmosis (RO). Un valor alto del SDI indica una mayor carga de contaminantes en el agua de alimentación, lo que puede afectar la eficiencia y la vida útil del sistema RO.\n\nLos contaminantes comunes que contribuyen al valor del SDI incluyen:\n- Nitratos\n- Fosfatos\n- Cloruros\n- Sulfatos\n- Carbonatos\n- Iones metálicos (como hierro y manganeso)\n- Amoníaco\n- Metales pesados (como plomo, cadmio, mercurio)\n\nUn SDI alto puede llevar a varios problemas, como:\n1. **Reducción de la Eficiencia**: Los contaminantes pueden acumularse en el membrana RO, reduciendo su capacidad para filtrar el agua.\n2. **Mayor Carga del Sistema**: La presencia de altos niveles de SDI puede requerir más frecuencia de reemplazo de membranas y

### Elegir mis embedding

In [9]:
available_embeddings =  {"gemma":"embeddings_gemma_y_metadatos","multilingual":"embeddings_y_metadatos"}

In [10]:
# Elegimos el embedding al usar
embedding = available_embeddings["gemma"]

### RAG System

In [11]:
import pickle
#Usaremos los embedding y metadatos usados anteriormente
with open(f"../outputs/{embedding}.pkl", "rb") as f:
    data = pickle.load(f)

embeddings = data["embeddings"]
metadatos = data["metadatos"]

In [12]:
#Uso FAISS para indexar
#FAISS es una librería desarrollada por Meta (Facebook) para hacer búsqueda rápida de vectores por similitud, ideal cuando tienes muchos embeddings (como en RAG).
import faiss
import numpy as np
embedding_matrix = np.array(embeddings)

# Crear índice FAISS (búsqueda por similitud L2 o Euclidiana)
dim = embedding_matrix.shape[1] 
print(dim)
index = faiss.IndexFlatL2(dim)  

# Agregar los vectores al índice
index.add(embedding_matrix)

# Guardar el índice en disco
faiss.write_index(index, "../outputs/faiss_index.index")

768


In [ ]:
# Obtengo las chunks mas relevantes y genero la pregunta al modelo 
def responder_con_phi4_con_contexto(pregunta, modelo_embedding, k=5, inEnglish= False):
    # Embeddear la pregunta
    pregunta_vec = modelo_embedding.encode([pregunta])

    # Buscar k chunks relevantes en FAISS
    D, I = index.search(np.array(pregunta_vec), k)

    # Recuperar los chunks y sus títulos
    chunks_usados = []
    contexto = ""

    for idx in I[0]:
        doc = metadatos[idx]
        chunk_text = doc["chunk"].strip()
        titulo = doc.get("id_doc", "Sin título")

        chunks_usados.append({
            "titulo": titulo,
            "chunk": chunk_text
        })

        contexto += f"- {chunk_text}\n"
    idioma = "La respuesta tiene que ser en ingles" if inEnglish else "" 

    # Construir prompt para Phi-4
    prompt = f"<|user|>\nUsa el siguiente contexto para responder la pregunta de manera clara y precisa.\n\nContexto:\n{contexto}\nPregunta: {pregunta} {idioma}\n<|assistant|>"
    
    # Generar respuesta
    output = generator(
        prompt,
        max_new_tokens=300,
        temperature=0.5,
        do_sample=True
    )[0]["generated_text"]

    respuesta = output[len(prompt):].strip()
 
    return {
        "pregunta": pregunta,
        "respuesta": respuesta,
        "chunks_usados": chunks_usados
    }

In [14]:
from sentence_transformers import SentenceTransformer
# Uso el modelo que use en el sentence embedding para codificar mi pregunta
modelo_embedding = SentenceTransformer("google/embeddinggemma-300m")

#Uso la misma pregunta que el caso anterior
resultado = responder_con_phi4_con_contexto(
    "¿Qué indica un valor alto del índice SDI en el agua de alimentación de RO?",
    modelo_embedding
)

print("🔹 Pregunta:", resultado["pregunta"])
print("📣 Respuesta generada:\n", resultado["respuesta"])
print("\n📚 Chunks utilizados:")
for i, chunk in enumerate(resultado["chunks_usados"], 1):
    print(f"{i}. 📝 Documento: {chunk['titulo']}\n   📄 Texto: {chunk['chunk'][:200]}...")


Un valor alto del índice SDI (Silt Density Index) en el agua de alimentación de la Reverse Osmosis (RO) indica una alta concentración de materia particulada en el agua. Esto sugiere un mayor riesgo de obstrucción de las membranas de RO y un mayor potencial de encrustación, lo que puede afectar la eficiencia del sistema de RO y potencialmente reducir su vida útil. El SDI mide la tasa de obstrucción de una membrana de filtro de 0.45 µm cuando se pasa agua a través de él a una presión constante, y valores altos indican una mayor necesidad de tratamiento de la fuente de agua para reducir el contenido de partículas antes del proceso de RO.
🔹 Pregunta: ¿Qué indica un valor alto del índice SDI en el agua de alimentación de RO?
📣 Respuesta generada:
 Un valor alto del índice SDI (Silt Density Index) en el agua de alimentación de la Reverse Osmosis (RO) indica una alta concentración de materia particulada en el agua. Esto sugiere un mayor riesgo de obstrucción de las membranas de RO y un mayor

### Evaluaremos Metrica

In [15]:
import pandas as pd
# Cargar el archivo CSV
df_qa = pd.read_csv("../dataQA/qa.txt")
df_qa.head()

chunk  \
0  seawater seawater tds mgl considered standard ...   
1  recovery limit salinity andor boron concentrat...   
2  design boynton beach fl membrane softening wat...   
3  range rather absolute value temperature variat...   
4  risk scaling due water scarcity environmental ...   

                                            question  \
0  What types of water are classified based on To...   
1  Why is it important to limit product recovery ...   
2  How is the maximum recovery value determined f...   
3  Why is average temperature used for performanc...   
4  Why must scaling substances be removed from tr...   

                                              answer  
0  Water is classified into categories like seawa...  
1  Limiting product recovery is important to ensu...  
2  The maximum recovery value is determined by co...  
3  Average temperature is used because membrane p...  
4  Even after secondary treatment, wastewater can...

In [16]:
df_qa.describe()

chunk  \
count                                                 511   
unique                                                511   
top     seawater seawater tds mgl considered standard ...   
freq                                                    1   

                                                 question  \
count                                                 511   
unique                                                511   
top     What types of water are classified based on To...   
freq                                                    1   

                                                   answer  
count                                                 511  
unique                                                511  
top     Water is classified into categories like seawa...  
freq                                                    1

### GENERACION RAG

In [17]:
import json
# Generaremos las respuestas con el modelo con RAG y lo almacenaremos
for i, row in df_qa.iterrows():
    pregunta = row["question"]
    resultado = responder_con_phi4_con_contexto(pregunta, modelo_embedding,5,True)
    df_qa.at[i, "answer_modelo_rag"] = resultado["respuesta"]
    df_qa.at[i, "retrieved"] = json.dumps(resultado["chunks_usados"])

La respuesta tiene que ser en ingles
Based on Total Dissolved Solids (TDS) levels, water can be classified into three main categories:

1. Brackish Water: TDS levels are between 1,000 and 10,000 mg/L. This type of water has more dissolved solids than freshwater but less than seawater.

2. Fresh Water: TDS levels are below 1,000 mg/L. This includes rivers, lakes, and streams that have low concentrations of dissolved solids.

3. Seawater: TDS levels are typically around 35,000 to 40,000 mg/L. This classification is based on the average TDS concentration of ocean water.
La respuesta tiene que ser en ingles
Limiting product recovery in reverse osmosis (RO) systems is important for several reasons:

1. Scaling Prevention: As recovery increases, the concentration of sparingly soluble salts in the concentrate stream also increases. If the concentration exceeds the solubility limit of these salts, scaling occurs, which can reduce the efficiency of the RO system and lead to membrane fouling.

2

You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


The effectiveness of antiscalants in RO (Reverse Osmosis) systems is influenced by several factors:

1. **Chemical Composition**: The choice of antiscalant, whether it is anionic, nonionic, or organophosphonate, can affect its interaction with scaling ions and its overall effectiveness.

2. **Ionic Strength**: The ionic strength of the feed water can impact the performance of antiscalants, as it may influence the degree of interference with the RO membranes.

3. **Concentration and Dosage**: Proper dosing of antiscalants is crucial. Overdosing can lead to decreased efficiency and the formation of gumlike products that are difficult to remove, while underdosing may not prevent scaling effectively.

4. **Compatibility with Polymers**: When adding anionic scale inhibitors, it is important to ensure that no significant amounts of cationic polymers are present, as they can react with the scale inhibitors and reduce their effectiveness.

5. **Feed Water Quality**: The presence of suspended m

In [18]:
df_filtrado = df_qa[["chunk", "question", "answer","answer_modelo_rag"]]
df_filtrado.to_csv("../dataQA/df_qa_gemma.csv", index=False, encoding="utf-8")

### GENERACION MODELO SIN RAG

In [19]:
import json
# Generaremos las respuestas con el modelo con RAG y lo almacenaremos
for i, row in df_qa.iterrows():
    pregunta = row["question"]
    prompt = f"<|user|>\n{pregunta}\n<|assistant|>"
    resultado =  generator(prompt, max_new_tokens=300, do_sample=True, temperature=0.5)[0]["generated_text"]
    respuesta = resultado[len(prompt):].strip()
    df_qa.at[i, "answer_modelo"] = respuesta

In [20]:
df_qa.head()

chunk  \
0  seawater seawater tds mgl considered standard ...   
1  recovery limit salinity andor boron concentrat...   
2  design boynton beach fl membrane softening wat...   
3  range rather absolute value temperature variat...   
4  risk scaling due water scarcity environmental ...   

                                            question  \
0  What types of water are classified based on To...   
1  Why is it important to limit product recovery ...   
2  How is the maximum recovery value determined f...   
3  Why is average temperature used for performanc...   
4  Why must scaling substances be removed from tr...   

                                              answer  \
0  Water is classified into categories like seawa...   
1  Limiting product recovery is important to ensu...   
2  The maximum recovery value is determined by co...   
3  Average temperature is used because membrane p...   
4  Even after secondary treatment, wastewater can...   

                                   answer_modelo_rag  \
0  Based on Total Dissolved Solids (TDS) levels, ...   
1  Limiting product recovery in reverse osmosis (...   
2  El valor máximo de recuperación para sistemas ...   
3  The average temperature is used for performanc...   
4  Scaling substances must be removed from treate...   

                                           retrieved  \
0  [{"titulo": "7.5 RO FOULING substance (anaysis...   
1  [{"titulo": "7.5 RO FOULING substance (anaysis...   
2  [{"titulo": "7.5 RO FOULING substance (anaysis...   
3  [{"titulo": "7.5 RO FOULING substance (anaysis...   
4  [{"titulo": "7.5 RO FOULING substance (anaysis...   

                                       answer_modelo  
0  Total Dissolved Solids (TDS) levels are used t...  
1  Limiting product recovery in Reverse Osmosis (...  
2  Membrane softening systems, such as those used...  
3  The term "RO membranes" typically refers to re...  
4  In reverse osmosis (RO) systems, scaling subst...

In [21]:
df_qa.iloc[0]["retrieved"]

'[{"titulo": "7.5 RO FOULING substance (anaysis solution).pdf", "chunk": "d 4382 f 60 d 1498 calcium and magnesium chloride carbon dioxide , bicarbonate , carbonate phosphorus sulfate aluminum manganese silica dissolved oxygen iron fluoride cod residual chlorine ph lithium , potassium , sodium ammonia nitrogen particulate and dissolved matter turbidity total organic carbon toc arsenic boron strontium practices for sampling water nitrite nitrate silt density index barium microbiological contaminants in water oxidationreduction potential orp bod aoc standard methods 1 3500ca , mg 4500chloride 4500carbon dioxide , 2320 4500p 4500sulfate 3500al 3500mn 4500silica 4500o 3500fe 4500fluoride 5220 4500cl 4500ph value 3500li , na , k 45nh3 2560 2130 5310 3500as 4500b 3500sr 1060 4500nitrogen 3500ba 2580 5210 9217 2.3 scale control 2.3.1 introduction scaling of ronf membranes may occur when sparingly soluble salts are concentrated within the element beyond their solubility limit . for example , i

### Guardamos el df

In [22]:
df_filtrado = df_qa[["chunk", "question", "answer","answer_modelo"]]
df_filtrado.to_csv("../dataQA/df_qa.csv", index=False, encoding="utf-8")

## ROUGUE SCORE

In [23]:
import os
output_dir = os.path.join("..", "resultados")
# El ROUGE score (Recall-Oriented Understudy for Gisting Evaluation) es una métrica ampliamente usada para evaluar la calidad de textos generados automáticamente
from rouge_score import rouge_scorer
scorer = rouge_scorer.RougeScorer(["rouge1", "rouge2", "rougeL"], use_stemmer=True)
## Definimos funcion para hallar ROUGE
def calculate_rouge_score(column_name,data_name):
    # Evaluar ROUGE para cada par respuesta_modelo - respuesta_referencia
    rouge_scores = []
    
    for i, row in df_qa.iterrows():
        ref = row["answer"]  # respuesta de referencia
        gen = row[column_name]  # respuesta generada
        score = scorer.score(ref, gen)
        rouge_scores.append({
            "ROUGE-1": score["rouge1"].fmeasure,
            "ROUGE-2": score["rouge2"].fmeasure,
            "ROUGE-L": score["rougeL"].fmeasure
        })
        
    #Resultados
    # Convertir a DataFrame y unirlo al original
    df_rouge = pd.DataFrame(rouge_scores)
    df_resultado = pd.concat([df_qa.reset_index(drop=True), df_rouge], axis=1)

    # Mostrar puntajes promedio
    promedios = df_rouge.mean()
    print("🔍 Promedios ROUGE:")
    print(promedios.round(4))
    
    # Ver resultados por pregunta
    print("\n📌 Ejemplos con ROUGE:")
    print(df_resultado[["question", "ROUGE-1", "ROUGE-2", "ROUGE-L"]])

    # Guardar
    output_path = os.path.join(output_dir, data_name)
    df_resultado.to_csv(output_path, index=False)
    print(f"\n✅ Guardado en {data_name}")

### Evaluaremos ROUGUE SCORE sin RAG

In [24]:

#ROUGE-1
#¿Qué mide? Coincidencias de unigramas (palabras individuales).
#ROUGE-2
#¿Qué mide? Coincidencias de bigramas (pares de palabras consecutivas).
#ROUGE-L
#¿Qué mide? La subsecuencia común más larga (LCS) entre el texto generado y la referencia.

#| Métrica     | Bueno  | Muy bueno | Excelente |
#| ----------- | ------ | --------- | --------- |
#| **ROUGE-1** | > 0.40 | > 0.50    | > 0.60    |
#| **ROUGE-2** | > 0.20 | > 0.30    | > 0.40    |
#| **ROUGE-L** | > 0.30 | > 0.40    | > 0.50    |
calculate_rouge_score("answer_modelo","evaluacion_con_rouge.csv")

🔍 Promedios ROUGE:
ROUGE-1    0.1307
ROUGE-2    0.0301
ROUGE-L    0.0923
dtype: float64

📌 Ejemplos con ROUGE:
                                              question   ROUGE-1   ROUGE-2  \
0    What types of water are classified based on To...  0.164706  0.055336   
1    Why is it important to limit product recovery ...  0.134276  0.035587   
2    How is the maximum recovery value determined f...  0.132296  0.054902   
3    Why is average temperature used for performanc...  0.162791  0.046875   
4    Why must scaling substances be removed from tr...  0.143939  0.038168   
..                                                 ...       ...       ...   
506  What are common causes for failed serial commu...  0.122744  0.021818   
507  How should you troubleshoot incorrect output b...  0.209302  0.046875   
508  How can you fix alarm and control mode issues ...  0.149813  0.022642   
509  What steps can correct poor control accuracy o...  0.098361  0.000000   
510  How should error messages 

### Evaluaremos ROUGUE SCORE con RAG

In [25]:
calculate_rouge_score("answer_modelo_rag","evaluacion_rag_con_rouge.csv")

🔍 Promedios ROUGE:
ROUGE-1    0.2063
ROUGE-2    0.0765
ROUGE-L    0.1551
dtype: float64

📌 Ejemplos con ROUGE:
                                              question   ROUGE-1   ROUGE-2  \
0    What types of water are classified based on To...  0.304000  0.065041   
1    Why is it important to limit product recovery ...  0.154930  0.049645   
2    How is the maximum recovery value determined f...  0.007092  0.000000   
3    Why is average temperature used for performanc...  0.272727  0.076923   
4    Why must scaling substances be removed from tr...  0.251656  0.040268   
..                                                 ...       ...       ...   
506  What are common causes for failed serial commu...  0.176245  0.054054   
507  How should you troubleshoot incorrect output b...  0.175439  0.056537   
508  How can you fix alarm and control mode issues ...  0.236220  0.103175   
509  What steps can correct poor control accuracy o...  0.150943  0.007605   
510  How should error messages 

In [26]:
df_qa["question"][1]

'Why is it important to limit product recovery in RO systems?'

In [27]:
df_qa["answer"][1]

'Limiting product recovery is important to ensure the salinity and boron levels in the product water meet required standards, as exceeding recovery limits may compromise water quality depending on site-specific conditions.'

In [28]:
df_qa["answer_modelo_rag"][1]

'Limiting product recovery in reverse osmosis (RO) systems is important for several reasons:\n\n1. Scaling Prevention: As recovery increases, the concentration of sparingly soluble salts in the concentrate stream also increases. If the concentration exceeds the solubility limit of these salts, scaling occurs, which can reduce the efficiency of the RO system and lead to membrane fouling.\n\n2. Membrane Life: High recovery rates can lead to increased pressure and concentration of contaminants, which can accelerate membrane degradation and shorten the lifespan of the RO membranes.\n\n3. Energy Consumption: Higher recovery rates often require higher feed pressures, which in turn increases energy consumption. This can make the RO process less energy-efficient and more costly.\n\n4. Product Quality: High recovery rates can result in a higher concentration of contaminants in the product water, which may not meet the required quality standards for its intended use.\n\n5. Operational Costs: To 

Aunque semanticamente el texto generado es parcialmente similar y tecnicamente correcto, el ROUGE bajo es justificado ya que muchas palabras no coincide y la estructura no coincide(gramaticalmente incorrecta), se evaluara modificar el prompt, ademas de implementar tecnicas de evaluacion del contexto extraido por el Retriever como el DSLR y finalmente el finetunning.

### BERT SCORE

In [ ]:
### Definimos funcion que me calcula y muestra BERTSCORE
from bert_score import score
def calculate_bert_score(name_column,name_data):
    # Evaluar BERT SCORE para cada par respuesta_modelo - respuesta_referencia
    bert_scores = []
    for i, row in df_qa.iterrows():
       
        ref = row["answer"]  # respuesta de referencia
        gen = row[name_column]  # respuesta generada
        P, R, F1 = score([gen], [ref], lang="en",verbose=False)
        bert_scores.append({
            "PRECISION": P.item(),
            "RECALL": R.item(),
            "F1": F1.item()
        })
        
    
    #Resultados
    # Convertir a DataFrame y unirlo al original
    df_bert = pd.DataFrame(bert_scores)
    df_resultado_bert = pd.concat([df_qa.reset_index(drop=True), df_bert], axis=1)

    # Mostrar puntajes promedio
    promedios = df_bert.mean()
    print("🔍 Promedios BERTSCORE:")
    print(promedios.round(4))
    # Ver resultados por pregunta
    print("\n📌 Ejemplos con BERT:")
    print(df_resultado_bert[["question", "PRECISION", "RECALL", "F1"]])
    # Guardar
    output_path = os.path.join(output_dir, name_data)
    df_resultado_bert.to_csv(output_path, index=False)
    

### Calculamos BERT SCORE sin RAG

In [30]:
calculate_bert_score("answer_modelo","evaluacion_con_bert.csv")

Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You sho

🔍 Promedios BERTSCORE:
PRECISION    0.8021
RECALL       0.8555
F1           0.8277
dtype: float64

📌 Ejemplos con BERT:
                                              question  PRECISION    RECALL  \
0    What types of water are classified based on To...   0.792467  0.856142   
1    Why is it important to limit product recovery ...   0.817806  0.866466   
2    How is the maximum recovery value determined f...   0.804351  0.869390   
3    Why is average temperature used for performanc...   0.802974  0.864146   
4    Why must scaling substances be removed from tr...   0.810864  0.893190   
..                                                 ...        ...       ...   
506  What are common causes for failed serial commu...   0.813546  0.853682   
507  How should you troubleshoot incorrect output b...   0.802568  0.879966   
508  How can you fix alarm and control mode issues ...   0.786053  0.834939   
509  What steps can correct poor control accuracy o...   0.776231  0.832116   
510  How sh

### Calculamos BERT SCORE RAG

In [31]:
calculate_bert_score("answer_modelo_rag","evaluacion_rag_con_bert.csv")

Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You sho

🔍 Promedios BERTSCORE:
PRECISION    0.8245
RECALL       0.8817
F1           0.8519
dtype: float64

📌 Ejemplos con BERT:
                                              question  PRECISION    RECALL  \
0    What types of water are classified based on To...   0.823222  0.868404   
1    Why is it important to limit product recovery ...   0.818509  0.885625   
2    How is the maximum recovery value determined f...   0.717784  0.849334   
3    Why is average temperature used for performanc...   0.850824  0.903132   
4    Why must scaling substances be removed from tr...   0.851244  0.902692   
..                                                 ...        ...       ...   
506  What are common causes for failed serial commu...   0.823733  0.873221   
507  How should you troubleshoot incorrect output b...   0.821674  0.887254   
508  How can you fix alarm and control mode issues ...   0.793203  0.871294   
509  What steps can correct poor control accuracy o...   0.801440  0.851613   
510  How sh

### FRANQ 

In [32]:
import re
#Genero el prompt para generar los claims
def generar_prompt_atomic_claims(texto: str) -> str:
    prompt = f"""Your task is to extract atomic factual claims from the input text.

Each claim must:
1. **Atomicity**: Break down each statement into the smallest possible unit of factual information. Avoid grouping multiple facts in one claim.
2. **Context-Independent**: Each claim must be understandable and verifiable on its own without requiring additional context.
3. **Precise and Unambiguous**: Ensure the claims are specific and avoid combining related ideas.
4. **No Formatting**: The response must be a Python list of strings without any extra formatting, code blocks, or labels like "python".
5. **Boudaries**: The upper boundary must be 4 claims at most.

### Example:
If the input text is:
"Mary is a five-year-old girl. She likes playing piano and doesn’t like cookies."

The output of the example should be:
["Mary is a five-year-old girl.", "Mary likes playing piano.", "Mary doesn’t like cookies."]

Note that your response will be passed to the python interpreter, SO NO OTHER WORDS!
Also note that this is an example just to clarify how do I want the final output, so the final output must not be ["Mary is a five-year-old girl.", "Mary likes playing piano.", "Mary doesn’t like cookies."]
### Input:
{texto}

This is the final output and must not be the output of the example ["Mary is a five-year-old girl.", "Mary likes playing piano.", "Mary doesn’t like cookies."]
### Output:"""
    return prompt.strip()



def extraer_claims_con_phi4(respuesta_rag, generator, max_new_tokens=256):
    prompt = generar_prompt_atomic_claims(respuesta_rag)

    output = generator(
        prompt,
        max_new_tokens=max_new_tokens,
        do_sample=False,
        truncation=True
    )[0]["generated_text"]
    
    print(output)
    try:
        listas = re.findall(r"\[[^\[\]]+\]", output, re.DOTALL)
        print(listas)
        if listas:
            claims = eval(listas[-1])  
        else:
            print("⚠️ No se encontro una lista:")
            
            claims = []
    except Exception as e:
        print("⚠️ Error procesando claims. Output:")
        print(output)
        claims = []

    return claims

In [33]:
df_qa["claims_phi4"] = None  
# Usa la funcion generar los claims y almacenarlos en el Data Frame
for i, row in df_qa.iterrows():
    respuesta = row["answer_modelo_rag"]
    claims = extraer_claims_con_phi4(respuesta, generator)
    df_qa.at[i, "claims_phi4"] = claims

The following generation flags are not valid and may be ignored: ['temperature']. Set `TRANSFORMERS_VERBOSITY=info` for more details.


Your task is to extract atomic factual claims from the input text.

Each claim must:
1. **Atomicity**: Break down each statement into the smallest possible unit of factual information. Avoid grouping multiple facts in one claim.
2. **Context-Independent**: Each claim must be understandable and verifiable on its own without requiring additional context.
3. **Precise and Unambiguous**: Ensure the claims are specific and avoid combining related ideas.
4. **No Formatting**: The response must be a Python list of strings without any extra formatting, code blocks, or labels like "python".
5. **Boudaries**: The upper boundary must be 4 claims at most.

### Example:
If the input text is:
"Mary is a five-year-old girl. She likes playing piano and doesn’t like cookies."

The output of the example should be:
["Mary is a five-year-old girl.", "Mary likes playing piano.", "Mary doesn’t like cookies."]

Note that your response will be passed to the python interpreter, SO NO OTHER WORDS!
Also note tha

In [34]:
df_qa.iloc[1]["claims_phi4"]

['Limiting product recovery in RO systems is important for preventing scaling.',
 'High recovery rates can lead to increased pressure and concentration of contaminants.',
 'Higher recovery rates often require higher feed pressures, increasing energy consumption.',
 'Limiting recovery helps to ensure that the system operates within its designed parameters.']

In [35]:
df_qa

chunk  \
0    seawater seawater tds mgl considered standard ...   
1    recovery limit salinity andor boron concentrat...   
2    design boynton beach fl membrane softening wat...   
3    range rather absolute value temperature variat...   
4    risk scaling due water scarcity environmental ...   
..                                                 ...   
506  check wire size . check for bad connections . ...   
507  verify correct connections and test wiring pat...   
508  the output parameter settings . watlow series ...   
509  set the desired hysteresis value . the cycle t...   
510  set point . parameter lockout is active . set ...   

                                              question  \
0    What types of water are classified based on To...   
1    Why is it important to limit product recovery ...   
2    How is the maximum recovery value determined f...   
3    Why is average temperature used for performanc...   
4    Why must scaling substances be removed from tr...   
..                                                 ...   
506  What are common causes for failed serial commu...   
507  How should you troubleshoot incorrect output b...   
508  How can you fix alarm and control mode issues ...   
509  What steps can correct poor control accuracy o...   
510  How should error messages like ERIN, ERAB, or ...   

                                                answer  \
0    Water is classified into categories like seawa...   
1    Limiting product recovery is important to ensu...   
2    The maximum recovery value is determined by co...   
3    Average temperature is used because membrane p...   
4    Even after secondary treatment, wastewater can...   
..                                                 ...   
506  Incorrect address or baud rate settings, rever...   
507  You should verify all wiring connections, chec...   
508  Adjust the alarm settings to the correct appli...   
509  You should verify control mode selection (PID ...   
510  You should inspect and correct sensor wiring, ...   

                                     answer_modelo_rag  \
0    Based on Total Dissolved Solids (TDS) levels, ...   
1    Limiting product recovery in reverse osmosis (...   
2    El valor máximo de recuperación para sistemas ...   
3    The average temperature is used for performanc...   
4    Scaling substances must be removed from treate...   
..                                                 ...   
506  Common causes for failed serial communication ...   
507  To troubleshoot incorrect output behavior on t...   
508  To fix alarm and control mode issues on the SD...   
509  To correct poor control accuracy or reversed r...   
510  To handle error messages like ERIN, ERAB, or E...   

                                             retrieved  \
0    [{"titulo": "7.5 RO FOULING substance (anaysis...   
1    [{"titulo": "7.5 RO FOULING substance (anaysis...   
2    [{"titulo": "7.5 RO FOULING substance (anaysis...   
3    [{"titulo": "7.5 RO FOULING substance (anaysis...   
4    [{"titulo": "7.5 RO FOULING substance (anaysis...   
..                                                 ...   
506  [{"titulo": "sd31_manual.pdf", "chunk": "contr...   
507  [{"titulo": "sd31_manual.pdf", "chunk": ". pul...   
508  [{"titulo": "sd31_manual.pdf", "chunk": "contr...   
509  [{"titulo": "sd31_manual.pdf", "chunk": "tempe...   
510  [{"titulo": "sd31_manual.pdf", "chunk": "set p...   

                                         answer_modelo  \
0    Total Dissolved Solids (TDS) levels are used t...   
1    Limiting product recovery in Reverse Osmosis (...   
2    Membrane softening systems, such as those used...   
3    The term "RO membranes" typically refers to re...   
4    In reverse osmosis (RO) systems, scaling subst...   
..                                                 ...   
506  The SD31 is a controller from Silicon Laborato...   
507  Troubleshooting incorrect output behavior on a...   
508  The SD31 controller, which is a model

In [36]:
# Guardar
df_qa.to_csv("../dataQA/df_qa_gemma.csv", index=False)

### Probabilidad Fidelidad: Usamos los claims para verificar si son fieles al contexto

In [37]:
from sentence_transformers import CrossEncoder

# Modelo general entrenado en Natural Language Inference (NLI)
model_align = CrossEncoder("cross-encoder/nli-roberta-base", max_length=512)

def evaluar_fidelidad_alignscore(claims, retrieved_text, model):
    pairs = [(claim, retrieved_text) for claim in claims]
    
    # Devuelve logit scores (o softmax de 3 clases si usamos `predict(probs=True)`)
    logits = model.predict(pairs, apply_softmax=True)
    
    # Extraemos la probabilidad de entailment (índice 2)
    entailment_scores = [score[2] for score in logits]
    return entailment_scores

In [38]:
import ast
import json

# Paso 1: Concatenar todos los chunks recuperados
retrieved_text = ""
for retrieved in json.loads(df_qa.iloc[242]["retrieved"]):
    retrieved_text += retrieved["chunk"] + "\n"

# Paso 2: Asegurarse de que los claims estén en formato lista
claims_raw = df_qa.iloc[242]["claims_phi4"]
claims = ast.literal_eval(claims_raw) if isinstance(claims_raw, str) else claims_raw

# Paso 3: Evaluar AlignScore
scores = evaluar_fidelidad_alignscore(claims, retrieved_text, model_align)

# Paso 4: Mostrar resultados
for c, s in zip(claims, scores):
    print(retrieved_text)
    print(f"Claim: {c}\nAlignScore: {s}\n")

e.g. , by monitoring of the oxidationredox potential orp . chlorination chemistry chlorine is most commonly available as chlorine gas and the hypochlorites of sodium and calcium . in water , they hydrolyze instantaneously to hypochlorous acid cl2 h2o hocl hcl naocl h2o hocl naoh caocl2 2 h2o 2 hocl caoh2 hypochlorous acid dissociates in water to hydrogen ions and hypochlorite ions hocl h ocl the sum of cl2 , naocl , caocl2 , hocl , and ocl is referred to as free available chlorine fac or free residual chlorine frc , expressed as mgl cl2 . as discussed later , chloramines are formed from the reaction of chlorine with ammonia compounds present in the water . these chlorineammonia compounds are referred to as combined available chlorine cac page 60 of 182 trademark of the dow chemical company form no . 609000710705 249 of 865 or combined residual chlorine crc . the sum of free and combined availableresidual chlorine is called the total residual chlorine trc . trc fac cac frc crc the germi

### Probabilidad condicional: Dado que no es fiel si es factual

In [39]:
import torch
import torch.nn.functional as F

def log_prob_claim(claim: str, prompt: str, model, tokenizer) -> float:
    # Pongo en modo evaluacion el modelo
    model.eval()
    device = next(model.parameters()).device
    # Quiero ver que tan probable es que a partir de mi pregunta se genere mis claim
    input_text = prompt + claim
    inputs = tokenizer(input_text, return_tensors="pt", truncation=True)
    input_ids = inputs["input_ids"].to(device)
    # Para modo inferencia
    with torch.no_grad():
        outputs = model(input_ids=input_ids, return_dict=True)

    logits = outputs.logits  # (1, seq_len, g)
    # Ajuste para alinear inputs y targets
    logits = logits[:, :-1, :]
    labels = input_ids[:, 1:]

    log_probs = F.log_softmax(logits, dim=-1)
    selected_log_probs = log_probs.gather(2, labels.unsqueeze(-1)).squeeze(-1)
    # Extraer la parte del claim
    prompt_len = len(tokenizer(prompt)["input_ids"])
    claim_log_probs = selected_log_probs[:, prompt_len:]
    print(claim_log_probs)

    if claim_log_probs.numel() == 0:
        return float("-inf")

    avg_log_prob = claim_log_probs.mean().item()
    return avg_log_prob


In [40]:
for claim in claims:
        avg_log_p = log_prob_claim(claim, df_qa.iloc[242]["question"], model_lm, tokenizer)
        joint_prob = torch.exp(torch.tensor(avg_log_p))
        print(f"→ joint p(c | x): {joint_prob:.10f}\n")


tensor([[-6.5234e-01, -6.3705e-04, -4.9688e+00, -5.7188e+00, -6.5918e-02,
         -1.8406e-04, -5.6250e-01]], device='cuda:0', dtype=torch.bfloat16)
→ joint p(c | x): 0.1806963086



### Probabilidad condicional: Dado que es fiel si es factual

In [41]:
nli_model = CrossEncoder("cross-encoder/nli-roberta-base", device="cuda" if torch.cuda.is_available() else "cpu")

def calcular_max_nli(claim: str, retrieved_chunks: list, model_nli) -> float:
    # Preparar pares (premisa, hipótesis)
    pairs = [(chunk["chunk"], claim) for chunk in retrieved_chunks]
    
    # Predecir probabilidades
    probs = model_nli.predict(pairs, apply_softmax=True)  # shape: (k, 3)

    max_score = 0.0
    for prob in probs:
        entail = prob[2]         # índice 2: entailment
        contradict = prob[0]     # índice 0: contradiction

        denom = entail + contradict
        if denom > 0:
            ratio = entail / denom
            max_score = max(max_score, ratio)

    return max_score

In [42]:
retrieved_chunks = []
for retrieved in json.loads(df_qa.iloc[0]["retrieved"]):
    retrieved_chunks.append({"chunk": retrieved["chunk"]})
for claim in claims:
    max_nli_score = calcular_max_nli(claim, retrieved_chunks, nli_model)
    print(f"✅ Claim: {claim}")
    print(f"→ MaxNLI Score: {max_nli_score:.4f}\n")

✅ Claim: CRC stands for Combined Available Chlorine.
→ MaxNLI Score: 0.6368



### FRANQ A NUESTRA DATA

In [43]:
def calcular_FRANQ_respuesta(claims, retrieved_chunks, question, model_align, model_nli, model_lm, tokenizer):
    franq_claims=[]
    # Concatenamos los chunks recuperados
    retrieved_text = "\n".join(chunk["chunk"] for chunk in retrieved_chunks)
    print(retrieved_text)
    for claim in claims:
        # AlignScore
        align = evaluar_fidelidad_alignscore([claim], retrieved_text, model_align)[0]

        # MaxNLI
        maxnli = calcular_max_nli(claim, retrieved_chunks, model_nli)

        # p(c | x)
        logp = log_prob_claim(claim, question, model_lm, tokenizer)

        # Normalizamos logp de [-10, 0] a [0, 1]
        logp_norm = max(min((logp + 10) / 10, 1), 0)

        # FRANQ individual para el claim
        fr_c = align * maxnli + (1 - align) * logp_norm
        franq_claims.append(fr_c)

    fr_score = np.mean(franq_claims)
    return fr_score

In [44]:
import pandas as pd
df_qa = pd.read_csv("../dataQA/df_qa_gemma.csv")

In [45]:
df_qa.head()

chunk  \
0  seawater seawater tds mgl considered standard ...   
1  recovery limit salinity andor boron concentrat...   
2  design boynton beach fl membrane softening wat...   
3  range rather absolute value temperature variat...   
4  risk scaling due water scarcity environmental ...   

                                            question  \
0  What types of water are classified based on To...   
1  Why is it important to limit product recovery ...   
2  How is the maximum recovery value determined f...   
3  Why is average temperature used for performanc...   
4  Why must scaling substances be removed from tr...   

                                              answer  \
0  Water is classified into categories like seawa...   
1  Limiting product recovery is important to ensu...   
2  The maximum recovery value is determined by co...   
3  Average temperature is used because membrane p...   
4  Even after secondary treatment, wastewater can...   

                                   answer_modelo_rag  \
0  Based on Total Dissolved Solids (TDS) levels, ...   
1  Limiting product recovery in reverse osmosis (...   
2  El valor máximo de recuperación para sistemas ...   
3  The average temperature is used for performanc...   
4  Scaling substances must be removed from treate...   

                                           retrieved  \
0  [{"titulo": "7.5 RO FOULING substance (anaysis...   
1  [{"titulo": "7.5 RO FOULING substance (anaysis...   
2  [{"titulo": "7.5 RO FOULING substance (anaysis...   
3  [{"titulo": "7.5 RO FOULING substance (anaysis...   
4  [{"titulo": "7.5 RO FOULING substance (anaysis...   

                                       answer_modelo  \
0  Total Dissolved Solids (TDS) levels are used t...   
1  Limiting product recovery in Reverse Osmosis (...   
2  Membrane softening systems, such as those used...   
3  The term "RO membranes" typically refers to re...   
4  In reverse osmosis (RO) systems, scaling subst...   

                                         claims_phi4  
0  ['Brackish Water TDS levels are between 1,000 ...  
1  ['Limiting product recovery in RO systems is i...  
2  ['El valor máximo de recuperación se determina...  
3  ['The average temperature is used for performa...  
4  ['Scaling substances must be removed from trea...

In [46]:
franq_scores = []
import numpy as np
import os
for i, row in df_qa.iterrows():
    try:
        # Parsear claims y chunks si están como strings
        claims_raw = row["claims_phi4"]
        claims = ast.literal_eval(claims_raw) if isinstance(claims_raw, str) else claims_raw

        retrieved_chunks_raw = row["retrieved"]
        retrieved_chunks = json.loads(retrieved_chunks_raw) if isinstance(retrieved_chunks_raw, str) else retrieved_chunks_raw

        # Calcular el score FRANQ para esa respuesta
        score = calcular_FRANQ_respuesta(
            claims=claims,
            retrieved_chunks=retrieved_chunks,
            question=row["question"],
            model_align=model_align,
            model_nli=nli_model,
            model_lm=model_lm,
            tokenizer=tokenizer
        )
    except Exception as e:
        print(f"⚠️ Error en fila {i}: {e}")
        score = None

    franq_scores.append(score)
# Convertir a DataFrame y unirlo al original
df_franq = pd.DataFrame(franq_scores)
df_resultado_franq = pd.concat([df_qa.reset_index(drop=True), df_franq], axis=1)

# Ver resultados por pregunta
print("\n📌 Ejemplos con FRANQ:")
print(df_resultado_franq)
# Guardar
output_path = os.path.join(output_dir, "evaluacion_rag_con_franq.csv")
df_resultado_franq.to_csv(output_path, index=False)


d 4382 f 60 d 1498 calcium and magnesium chloride carbon dioxide , bicarbonate , carbonate phosphorus sulfate aluminum manganese silica dissolved oxygen iron fluoride cod residual chlorine ph lithium , potassium , sodium ammonia nitrogen particulate and dissolved matter turbidity total organic carbon toc arsenic boron strontium practices for sampling water nitrite nitrate silt density index barium microbiological contaminants in water oxidationreduction potential orp bod aoc standard methods 1 3500ca , mg 4500chloride 4500carbon dioxide , 2320 4500p 4500sulfate 3500al 3500mn 4500silica 4500o 3500fe 4500fluoride 5220 4500cl 4500ph value 3500li , na , k 45nh3 2560 2130 5310 3500as 4500b 3500sr 1060 4500nitrogen 3500ba 2580 5210 9217 2.3 scale control 2.3.1 introduction scaling of ronf membranes may occur when sparingly soluble salts are concentrated within the element beyond their solubility limit . for example , if a reverse osmosis plant is operated at 50 recovery , the concentration i

In [47]:

df_franq.columns = ["franq_score"]
df_franq

franq_score
0       0.902642
1       0.912786
2       0.775722
3       0.895274
4       0.944809
..           ...
506     0.659882
507     0.776042
508     0.799601
509     0.825642
510     0.453564

[511 rows x 1 columns]

In [48]:
for i, row in df_qa.iloc[[114]].iterrows():
    respuesta = row["answer_modelo_rag"]
    
    claims = extraer_claims_con_phi4(respuesta, generator)
    
    df_qa.at[i, "claims_phi4"] = claims

Your task is to extract atomic factual claims from the input text.

Each claim must:
1. **Atomicity**: Break down each statement into the smallest possible unit of factual information. Avoid grouping multiple facts in one claim.
2. **Context-Independent**: Each claim must be understandable and verifiable on its own without requiring additional context.
3. **Precise and Unambiguous**: Ensure the claims are specific and avoid combining related ideas.
4. **No Formatting**: The response must be a Python list of strings without any extra formatting, code blocks, or labels like "python".
5. **Boudaries**: The upper boundary must be 4 claims at most.

### Example:
If the input text is:
"Mary is a five-year-old girl. She likes playing piano and doesn’t like cookies."

The output of the example should be:
["Mary is a five-year-old girl.", "Mary likes playing piano.", "Mary doesn’t like cookies."]

Note that your response will be passed to the python interpreter, SO NO OTHER WORDS!
Also note tha

In [49]:
df_franq[df_franq["franq_score"] < 0.5]

franq_score
45      0.236977
240     0.403539
260     0.495557
261     0.470304
264     0.442449
276     0.423203
277     0.443135
299     0.432954
305     0.479517
311     0.425835
316     0.373945
320     0.469890
322     0.498048
326     0.361263
333     0.392320
371     0.426114
395     0.466010
397     0.474185
400     0.494344
432     0.477428
510     0.453564

In [50]:
df_qa["claims_phi4"][114]

['TRC measurement supports RO system operation optimization.',
 'TRC is the maximum amount of water that can pass through the RO membrane before efficiency declines.',
 'TRC measurements help determine when RO membranes need replacement.',
 'TRC measurements can be used to monitor system efficiency.']

In [51]:
promedios = df_franq.mean()

promedios

franq_score    0.814019
dtype: float64

## REFINAMIENTO DOCUMENTOS EXTRAIDOS: DSLR

### Separamos los documentso recuperados en oraciones

In [52]:
import spacy
nlp = spacy.load("en_core_web_sm")

def dividir_oraciones(texto):
    doc = nlp(texto)
    return [sent.text.strip() for sent in doc.sents]

In [53]:
import json
## Dividiremos en oraciones un documento recuperado
lista_chunks = json.loads(df_qa["retrieved"][2])
lista_chunks[0]["chunk"]

'if sio2c is greater than sio2corr , silica scaling can occur and adjustment is required . adjustments for scale control if sio2c is less than sio2corr , a higher recovery can be used with respect to scaling by silica . reiteration of the calculations at higher recovery can be used to determine the maximum conversion with respect to scaling by silica . if sio2c is greater than sio2corr , a lower recovery must be used to prevent scaling . reiteration of the calculations can be used to determine the allowable recovery with respect to scaling by silica . if the maximum allowable recovery is lower than desired , lime plus soda ash softening employing either magnesium oxide or sodium aluminate can be used in the pretreatment system to decrease the sio2 concentration in the feed stream see section 2.3.6 and thus permit higher conversion with respect to scaling by silica . it is important that the softening process be performed properly in order to prevent formation of insoluble metal silicat

In [54]:
tokenized_chunk = dividir_oraciones(lista_chunks[0]["chunk"])
tokenized_chunk

['if sio2c is greater than sio2corr , silica scaling can occur and adjustment is required .',
 'adjustments for scale control if sio2c is less than sio2corr , a higher recovery can be used with respect to scaling by silica .',
 'reiteration of the calculations at higher recovery can be used to determine the maximum conversion with respect to scaling by silica .',
 'if sio2c is greater than sio2corr , a lower recovery must be used to prevent scaling .',
 'reiteration of the calculations can be used to determine the allowable recovery with respect to scaling by silica .',
 'if the maximum allowable recovery is lower than desired , lime plus soda ash softening employing either magnesium oxide or sodium aluminate can be used in the pretreatment system to decrease the sio2 concentration in the feed stream see section 2.3.6 and thus permit higher conversion with respect to scaling by silica .',
 'it is important that the softening process be performed properly in order to prevent formation o

### Usamos un modelo para el re ranking por similaridad

In [55]:
question = df_qa["question"][2]
df_qa["question"][2]

'How is the maximum recovery value determined for membrane softening systems?'

In [56]:
from sentence_transformers import CrossEncoder


def re_rank_oraciones(question, oraciones):
    reranker = CrossEncoder("cross-encoder/ms-marco-MiniLM-L-6-v2")
    pairs = [(question, sent) for sent in oraciones]
    scores = reranker.predict(pairs)
    ranked = sorted(zip(oraciones, scores), key=lambda x: x[1], reverse=True)
    return ranked

In [57]:
ranked_sentences=re_rank_oraciones(question,tokenized_chunk)
ranked_sentences

[('if the maximum allowable recovery is lower than desired , lime plus soda ash softening employing either magnesium oxide or sodium aluminate can be used in the pretreatment system to decrease the sio2 concentration in the feed stream see section 2.3.6 and thus permit higher conversion with respect to scaling by silica .',
  -0.57205415),
 ('reiteration of the calculations at higher recovery can be used to determine the maximum conversion with respect to scaling by silica .',
  -2.407671),
 ('reiteration of the calculations can be used to determine the allowable recovery with respect to scaling by silica .',
  -6.067547),
 ('it is important that the softening process be performed properly in order to prevent formation of insoluble metal silicates in the reverse osmosis system .',
  -7.327737),
 ('adjustments for scale control if sio2c is less than sio2corr , a higher recovery can be used with respect to scaling by silica .',
  -9.016836),
 ('if sio2c is greater than sio2corr , a lower

### Filtramos las oracion con treshold adaptativo(90% percentil)



In [58]:
import numpy as np

def filtrar_por_umbral(oraciones_ranked, percentil=90):
    scores = [score for _, score in oraciones_ranked]
    umbral = np.percentile(scores, percentil)
    oraciones_filtradas = [(sent, score) for sent, score in oraciones_ranked if score >= umbral]
    return oraciones_filtradas, umbral

In [59]:
filtered_sentences,treshhold=filtrar_por_umbral(ranked_sentences)
filtered_sentences

[('if the maximum allowable recovery is lower than desired , lime plus soda ash softening employing either magnesium oxide or sodium aluminate can be used in the pretreatment system to decrease the sio2 concentration in the feed stream see section 2.3.6 and thus permit higher conversion with respect to scaling by silica .',
  -0.57205415)]

### Reconstruccion orden original

In [60]:
def reconstruir_contexto(oraciones_filtradas, oraciones_originales):
    oraciones_validas = set([sent for sent, _ in oraciones_filtradas])
    reconstruido = [sent for sent in oraciones_originales if sent in oraciones_validas]
    return reconstruido

In [61]:
refined_chunks=reconstruir_contexto(filtered_sentences,tokenized_chunk)
refined_chunks

['if the maximum allowable recovery is lower than desired , lime plus soda ash softening employing either magnesium oxide or sodium aluminate can be used in the pretreatment system to decrease the sio2 concentration in the feed stream see section 2.3.6 and thus permit higher conversion with respect to scaling by silica .']

## Aplicamos DSLR a nuestro Pipeline

In [62]:
## Funcion para implementar los 3 pasos de DSLR 
def refine_documents(sentence,pregunta):
    # Paso 1: Separar oraciones
    oraciones = dividir_oraciones(sentence)

    # Paso 2: Rankear oraciones
    oraciones_ranked = re_rank_oraciones(pregunta, oraciones)

    # Paso 3: Filtrar con percentil 90
    oraciones_filtradas, umbral = filtrar_por_umbral(oraciones_ranked, percentil=90)

    # Paso 4: Reconstruir en orden original
    oraciones_reconstruidas = reconstruir_contexto(oraciones_filtradas, oraciones)

    # Resultado final para pasar al LLM
    documento_refinado = " ".join(oraciones_reconstruidas)
    return documento_refinado
         
    

In [ ]:
## Implementamos DSLR en nuestro pipeline
def responder_con_phi4_con_contexto_refinado(pregunta, modelo_embedding, k=5, inEnglish= False):
     # Embeddear la pregunta
    pregunta_vec = modelo_embedding.encode([pregunta])

    # Buscar k chunks relevantes en FAISS
    D, I = index.search(np.array(pregunta_vec), k)

    # Recuperar los chunks y sus títulos
    chunks_usados = []
    contexto = ""
    for idx in I[0]:
        doc = metadatos[idx]
        chunk_text = doc["chunk"].strip()
        titulo = doc.get("id_doc", "Sin título")

        chunks_usados.append({
            "titulo": titulo,
            "chunk": chunk_text
        })
    chunk_filtrado = [] 
    for document in chunks_usados:
        texto_refinado=refine_documents(document["chunk"],pregunta)
        chunk_filtrado.append({
            "titulo": titulo,
            "chunk": texto_refinado
        })
        contexto += f"- {texto_refinado}\n"
    idioma = "La respuesta tiene que ser obligatoriamente en ingles" if inEnglish else "" 
    # Construir prompt para Phi-4
    prompt = f"<|user|>\nUsa el siguiente contexto para responder la pregunta de manera clara y precisa.\n\nContexto:\n{contexto}\nPregunta: {pregunta} {idioma}\n<|assistant|>"
    
    # Generar respuesta
    output = generator(
        prompt,
        max_new_tokens=300,
        temperature=0.5,
        do_sample=True
    )[0]["generated_text"]

    respuesta = output[len(prompt):].strip()

    return {
        "pregunta": pregunta,
        "respuesta": respuesta,
        "chunks_usados": chunk_filtrado
    }

In [64]:
import json
# Generaremos las respuestas con el modelo con RAG y lo almacenaremos
for i, row in df_qa.iterrows():
    pregunta = row["question"]
    resultado = responder_con_phi4_con_contexto_refinado(pregunta, modelo_embedding,5,True)
    df_qa.at[i, "answer_modelo_rag_dslr"] = resultado["respuesta"]
    df_qa.at[i, "retrieved_dslr"] = json.dumps(resultado["chunks_usados"])

La respuesta tiene que ser obligatoriamente en ingles
Water can be classified based on Total Dissolved Solids (TDS) levels into three main categories:

1. Freshwater: TDS levels below 1,000 milligrams per liter (mg/L)
2. Brackish water: TDS levels between 1,000 and 10,000 mg/L
3. Saline water: TDS levels above 10,000 mg/L

In the provided context, an example of brackish water composition is given with a TDS level of 478 mg/L, indicating that it falls within the brackish water category. Another example of well water with a TDS level of 325 mg/L would also be classified as brackish water.
La respuesta tiene que ser obligatoriamente en ingles
Limiting product recovery in RO (Reverse Osmosis) systems is important to minimize precipitation and scaling. This is crucial because exceeding the solubility limits of sparingly soluble salts, such as calcium carbonate and calcium sulfate, can lead to the formation of these compounds. This scaling can cause serious problems in the RO plant, includin

In [65]:
df_qa.head()

chunk  \
0  seawater seawater tds mgl considered standard ...   
1  recovery limit salinity andor boron concentrat...   
2  design boynton beach fl membrane softening wat...   
3  range rather absolute value temperature variat...   
4  risk scaling due water scarcity environmental ...   

                                            question  \
0  What types of water are classified based on To...   
1  Why is it important to limit product recovery ...   
2  How is the maximum recovery value determined f...   
3  Why is average temperature used for performanc...   
4  Why must scaling substances be removed from tr...   

                                              answer  \
0  Water is classified into categories like seawa...   
1  Limiting product recovery is important to ensu...   
2  The maximum recovery value is determined by co...   
3  Average temperature is used because membrane p...   
4  Even after secondary treatment, wastewater can...   

                                   answer_modelo_rag  \
0  Based on Total Dissolved Solids (TDS) levels, ...   
1  Limiting product recovery in reverse osmosis (...   
2  El valor máximo de recuperación para sistemas ...   
3  The average temperature is used for performanc...   
4  Scaling substances must be removed from treate...   

                                           retrieved  \
0  [{"titulo": "7.5 RO FOULING substance (anaysis...   
1  [{"titulo": "7.5 RO FOULING substance (anaysis...   
2  [{"titulo": "7.5 RO FOULING substance (anaysis...   
3  [{"titulo": "7.5 RO FOULING substance (anaysis...   
4  [{"titulo": "7.5 RO FOULING substance (anaysis...   

                                       answer_modelo  \
0  Total Dissolved Solids (TDS) levels are used t...   
1  Limiting product recovery in Reverse Osmosis (...   
2  Membrane softening systems, such as those used...   
3  The term "RO membranes" typically refers to re...   
4  In reverse osmosis (RO) systems, scaling subst...   

                                         claims_phi4  \
0  ['Brackish Water TDS levels are between 1,000 ...   
1  ['Limiting product recovery in RO systems is i...   
2  ['El valor máximo de recuperación se determina...   
3  ['The average temperature is used for performa...   
4  ['Scaling substances must be removed from trea...   

                              answer_modelo_rag_dslr  \
0  Water can be classified based on Total Dissolv...   
1  Limiting product recovery in RO (Reverse Osmos...   
2  La máxima recuperación permitida para sistemas...   
3  The average temperature is used for performanc...   
4  Scaling substances must be removed from treate...   

                                      retrieved_dslr  
0  [{"titulo": "7.5 RO FOULING substance (anaysis...  
1  [{"titulo": "7.5 RO FOULING substance (anaysis...  
2  [{"titulo": "7.5 RO FOULING substance (anaysis...  
3  [{"titulo": "7.5 RO FOULING substance (anaysis...  
4  [{"titulo": "7.5 RO FOULING substance (anaysis...

In [66]:
# Guardar
df_qa.to_csv("../dataQA/df_qa_gemma.csv", index=False)

In [67]:
index=0

In [68]:
df_qa["question"][index]

'What types of water are classified based on Total Dissolved Solids (TDS) levels?'

In [69]:
df_qa["answer"][index]

'Water is classified into categories like seawater, brackish water, slightly saline water, estuarine water, and salt lake water based on its TDS levels, which are estimated using conductivity and a conversion factor.'

In [70]:
df_qa["answer_modelo_rag_dslr"][index]

'Water can be classified based on Total Dissolved Solids (TDS) levels into three main categories:\n\n1. Freshwater: TDS levels below 1,000 milligrams per liter (mg/L)\n2. Brackish water: TDS levels between 1,000 and 10,000 mg/L\n3. Saline water: TDS levels above 10,000 mg/L\n\nIn the provided context, an example of brackish water composition is given with a TDS level of 478 mg/L, indicating that it falls within the brackish water category. Another example of well water with a TDS level of 325 mg/L would also be classified as brackish water.'

In [71]:
df_qa["answer_modelo_rag"][index]

'Based on Total Dissolved Solids (TDS) levels, water can be classified into three main categories:\n\n1. Brackish Water: TDS levels are between 1,000 and 10,000 mg/L. This type of water has more dissolved solids than freshwater but less than seawater.\n\n2. Fresh Water: TDS levels are below 1,000 mg/L. This includes rivers, lakes, and streams that have low concentrations of dissolved solids.\n\n3. Seawater: TDS levels are typically around 35,000 to 40,000 mg/L. This classification is based on the average TDS concentration of ocean water.'

In [72]:
df_qa["answer_modelo"][index]

'Total Dissolved Solids (TDS) levels are used to classify water quality in terms of its purity and suitability for various uses. TDS is a measure of the combined content of all inorganic and organic substances contained in a liquid. The classification of water based on TDS levels is as follows:\n\n\n- **Freshwater:** TDS levels of less than 1,000 milligrams per liter (mg/L) or parts per million (ppm). This water is typically very pure and is suitable for drinking, cooking, and most household uses.\n\n- **Slightly Saline Water:** TDS levels ranging from 1,000 to 3,000 mg/L. This water may have some taste and odor and is often used for irrigation and industrial cooling.\n\n- **Moderately Saline Water:** TDS levels between 3,000 and 10,000 mg/L. This water may have a noticeable taste and is generally not suitable for drinking or cooking but may be used for agricultural purposes.\n\n- **Highly Saline Water:** TDS levels between 10,000 and 35,000 mg/L. This water typically has a salty taste

## Calculamos metricas RAG + DSLR

### ROUGE SCORE

In [73]:
calculate_rouge_score("answer_modelo_rag_dslr","evaluacion_rag_dslr_con_rouge.csv")

🔍 Promedios ROUGE:
ROUGE-1    0.2160
ROUGE-2    0.0682
ROUGE-L    0.1589
dtype: float64

📌 Ejemplos con ROUGE:
                                              question   ROUGE-1   ROUGE-2  \
0    What types of water are classified based on To...  0.259542  0.062016   
1    Why is it important to limit product recovery ...  0.252252  0.128440   
2    How is the maximum recovery value determined f...  0.000000  0.000000   
3    Why is average temperature used for performanc...  0.272109  0.096552   
4    Why must scaling substances be removed from tr...  0.262295  0.050000   
..                                                 ...       ...       ...   
506  What are common causes for failed serial commu...  0.145455  0.037037   
507  How should you troubleshoot incorrect output b...  0.150198  0.039841   
508  How can you fix alarm and control mode issues ...  0.243655  0.102564   
509  What steps can correct poor control accuracy o...  0.100000  0.000000   
510  How should error messages 

### BERT SCORE

In [77]:
calculate_bert_score("answer_modelo_rag_dslr","evaluacion_rag_dslr_con_bert.csv")

Water is classified into categories like seawater, brackish water, slightly saline water, estuarine water, and salt lake water based on its TDS levels, which are estimated using conductivity and a conversion factor.
Water can be classified based on Total Dissolved Solids (TDS) levels into three main categories:

1. Freshwater: TDS levels below 1,000 milligrams per liter (mg/L)
2. Brackish water: TDS levels between 1,000 and 10,000 mg/L
3. Saline water: TDS levels above 10,000 mg/L

In the provided context, an example of brackish water composition is given with a TDS level of 478 mg/L, indicating that it falls within the brackish water category. Another example of well water with a TDS level of 325 mg/L would also be classified as brackish water.


Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Limiting product recovery is important to ensure the salinity and boron levels in the product water meet required standards, as exceeding recovery limits may compromise water quality depending on site-specific conditions.
Limiting product recovery in RO (Reverse Osmosis) systems is important to minimize precipitation and scaling. This is crucial because exceeding the solubility limits of sparingly soluble salts, such as calcium carbonate and calcium sulfate, can lead to the formation of these compounds. This scaling can cause serious problems in the RO plant, including reduced efficiency and potential damage to the system. Additionally, establishing well-designed scale control measures helps to ensure the longevity and effectiveness of the RO system.


Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


The maximum recovery value is determined by considering the calcium concentration in the water and using a specific calculation method outlined in the relevant design standards.
La máxima recuperación permitida para sistemas de desalinización por membrana se determina en función de varios factores, incluyendo la calidad del agua de entrada, las especificaciones del sistema de membrana y las tolerancias operativas para la calidad del agua de salida. En el contexto proporcionado, si la recuperación máxima deseada es menor que la permitida, se pueden emplear métodos de pretensión como el uso de lyes magnétiques o carbonato de sodio con soda, o el intercambio de cationes por resinas de ácido fuerte o débil, para reducir la concentración de sían en la corriente de alimentación y permitir una mayor conversión con respecto al escoramiento por sílice. La permeabilidad del sistema de membrana y la conductividad del peróxido también influyen en la determinación de la recuperación máxima, ya que 

...

You should verify control mode selection (PID or on/off), tune PID parameters, check thermocouple polarity, ensure correct input scaling, adjust cycle time, and confirm parameter lockout settings to access configurations.
To correct poor control accuracy or reversed readings on the SD31 controller, follow these steps:

1. Calibrate the SD31 controller using the front panel controls. Warm up the unit for 20 minutes before starting the calibration process. This ensures that the controller is properly warmed up for accurate calibration.
2. Follow the installation procedure exactly to guarantee a proper IP65N MA 4x seal, which ensures that the controller is installed in a protected environment.
3. If retrofitting the SD31 controller into an existing application, use a Watlow adapter plate to adapt it to the smaller controller size. This ensures that the SD31 controller fits properly in the existing setup.
4. Wire the controller correctly according to the specific model number of the SD31 c

Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


You should inspect and correct sensor wiring, ensure the correct sensor type is selected, restore factory calibration, maintain ambient temperature within operating limits, and reset or cycle power. If the issue persists, contact the manufacturer.
Error messages such as ERIN, ERAB, or ERCS on the SD31 controller indicate specific issues that need to be addressed:

- ERIN (Input Error): This message suggests that the sensor may be improperly wired. To handle this, check the wiring connections to ensure they are secure and correctly configured.

- ERAB (Ambient Temperature Error): This message indicates that the ambient temperature may be too hot or too cold for the sensor. To correct this, adjust the ambient temperature to a range that is suitable for the sensor's operation.

- ERCS (Checksum Error): This message implies that settings may have changed unexpectedly. To resolve this, review the current settings and compare them with the expected configuration to identify any discrepancies

Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


🔍 Promedios BERTSCORE:
PRECISION    0.8321
RECALL       0.8738
F1           0.8522
dtype: float64

📌 Ejemplos con BERT:
                                              question  PRECISION    RECALL  \
0    What types of water are classified based on To...   0.816443  0.869528   
1    Why is it important to limit product recovery ...   0.858346  0.889183   
2    How is the maximum recovery value determined f...   0.721848  0.850407   
3    Why is average temperature used for performanc...   0.847332  0.909696   
4    Why must scaling substances be removed from tr...   0.857442  0.900266   
..                                                 ...        ...       ...   
506  What are common causes for failed serial commu...   0.839590  0.845564   
507  How should you troubleshoot incorrect output b...   0.802643  0.866499   
508  How can you fix alarm and control mode issues ...   0.822337  0.861649   
509  What steps can correct poor control accuracy o...   0.809722  0.832345   
510  How sh

In [ ]:
from sentence_transformers import SentenceTransformer
# Uso el modelo que use en el sentence embedding para codificar mi pregunta
modelo_embedding = SentenceTransformer("google/embeddinggemma-300m")
# Generacion 
pregunta = "¿Qué indica un valor alto del índice SDI en el agua de alimentación de RO?"
resultado = responder_con_phi4_con_contexto_refinado(pregunta, modelo_embedding,5,True)
print("🔹 Pregunta:", resultado["pregunta"])
print("📣 Respuesta generada:\n", resultado["respuesta"])
print("\n📚 Chunks utilizados:")
for i, chunk in enumerate(resultado["chunks_usados"], 1):
    print(f"{i}. 📝 Documento: {chunk['titulo']}\n   📄 Texto: {chunk['chunk'][:200]}...")

c:\Users\PC\Maestria\NLP\RAG\venv\Lib\site-packages\huggingface_hub\file_download.py:143: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\PC\.cache\huggingface\hub\models--cross-encoder--ms-marco-MiniLM-L-6-v2. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)
Xet Storage is enabled for this repo, but the 'hf_xet' package is not installed. Falling back to regu

🔹 Pregunta: ¿Qué indica un valor alto del índice SDI en el agua de alimentación de RO?
📣 Respuesta generada:
 Un valor alto del Índice de Sólidos Dispersos (SDI) en el agua de alimentación de un sistema de Filtración de Oxígeno (RO) indica que hay un alto contenido de partículas minerales y otros disolutos en el agua. Esto puede afectar negativamente el rendimiento del sistema al causar obstrucciones, desgaste y reducción de la eficiencia de la filtración. Es esencial mantener un SDI bajo para asegurar un funcionamiento óptimo del sistema de RO.

📚 Chunks utilizados:
1. 📝 Documento: 7.5 RO FOULING substance (anaysis solution).pdf
   📄 Texto: . 23....
2. 📝 Documento: 7.5 RO FOULING substance (anaysis solution).pdf
   📄 Texto: water is drained from the system during startup and when water quality is not maintained . during initial...
3. 📝 Documento: 7.5 RO FOULING substance (anaysis solution).pdf
   📄 Texto: 8 eq . 3 eq ....
4. 📝 Documento: 7.5 RO FOULING substance (anaysis solution).pdf